# PROCESAMIENTO DE FEATURES

In [13]:
import os
! git clone https://github.com/v-iashin/video_features.git
! pip install omegaconf==2.0.6 av==10.0

fatal: destination path 'video_features' already exists and is not an empty directory.


DEPRECATION: omegaconf 2.0.6 has a non-standard dependency specifier PyYAML>=5.1.*. pip 24.1 will enforce this behaviour change. A possible replacement is to upgrade to a newer version of omegaconf or contact the author to suggest that they release a version with a conforming dependency specifiers. Discussion can be found at https://github.com/pypa/pip/issues/12063


In [14]:
%cd video_features
%pwd

f:\Machine_learning\P_3\video_features


d:\Semestre_2024-1_CS\ML\Projetcs\Project1\penv\Lib\site-packages\IPython\core\magics\osm.py:417: UserWarning: This is now an optional IPython functionality, setting dhist requires you to install the `pickleshare` library.
  self.shell.db['dhist'] = compress_dhist(dhist)[-100:]


'f:\\Machine_learning\\P_3\\video_features'

In [15]:
import os
print(os.getcwd())
os.chdir('F:\Machine_learning\P_3\\video_features')# La libreria Video_features tiene su propio repositorio todos los derechos a ellos
print(os.getcwd())

f:\Machine_learning\P_3\video_features
f:\Machine_learning\P_3\video_features


In [16]:
from video_features.models.r21d.extract_r21d import ExtractR21D
from video_features.utils.utils import build_cfg_path
from omegaconf import OmegaConf
import pandas as pd
import torch

device = 'cuda:0' if torch.cuda.is_available() else 'cpu'
torch.cuda.get_device_name(0)

'NVIDIA GeForce RTX 4080'

# Add all the videos to process the features

In [2]:
import  os
import numpy as np

import shutil
print(os.getcwd())
os.chdir('F:\\Machine_learning\\P_3') #use your local machine path 


source_dir = 'train_subset'
target_dir1 = 'train_subset_1' #Lote para Fabricio
target_dir2 = 'train_subset_2'  #Lote para Jesus



path = os.getcwd()
files = os.listdir(path+'\\'+source_dir)

print(os.getcwd())





# Create target directories if they don't exist
os.makedirs(target_dir1, exist_ok=True)
os.makedirs(target_dir2, exist_ok=True)

print("Total  train list ",len(files))

# Split the files into two equal parts
midpoint = len(files) // 2
files_part1 = files[:midpoint]
files_part2 = files[midpoint:]

# Move the files to the respective target directories
for file in files_part1:
    shutil.move(os.path.join(source_dir, file), os.path.join(target_dir1, file))

for file in files_part2:
    shutil.move(os.path.join(source_dir, file), os.path.join(target_dir2, file))

print(f'Files have been divided and moved to {target_dir1} and {target_dir2}')



feature_path = "F:\\Machine_learning\\P_3\\train_subset_features" #use your local machine path 
train_path = "F:/Machine_learning/P_3/" + target_dir1 #use your local machine path  also  #Change here into part2 for Egus :3

if len(files_part1) ==0 : #Change here into part2 for Jesus :3 
    files_part1 = os.listdir(train_path)


if not os.path.exists(feature_path):
    os.makedirs(feature_path)

train_list = [os.path.join(train_path, f) for f in files_part1]
print("Your new work load is" ,train_path +'----->'+ str(len(train_list)))
if os.access(feature_path, os.W_OK):
    print(f"Tienes permisos de escritura en el directorio: {feature_path}")
else:
    print(f"No tienes permisos de escritura en el directorio: {feature_path}")    
    

In [30]:
#restore the old path 
os.chdir('F:\\Machine_learning\\P_3\\video_features') #use your local machine path 
print(os.getcwd())
print(feature_path) #use your local machine path 

In [31]:
# Load and adjust seetings
feature_type = 'r21d'
args = OmegaConf.load(build_cfg_path(feature_type))
args.video_paths = train_list
args.model_name = 'r2plus1d_18_16_kinetics'
args.device = device

# Load model
extractor = ExtractR21D(args)

# Dictionary to save all features
all_features = {}

# Proccesed video counter
processed_count = 0

# Extract featyres
for video_path in args.video_paths:
    processed_count += 1
    video_name = os.path.basename(video_path)
    

   
    try:
        feature_dict = extractor.extract(video_path)
        
        # Verify if features are being generated
        if not feature_dict:
            print(f"No se generaron características para {video_name}")
        else:
            for k, v in feature_dict.items():
              

                # Save them into a dictionary
                video_key = os.path.basename(video_name).replace('.mp4', '')
                if video_key not in all_features:
                    all_features[video_key] = {}
                    all_features[video_key][k] = v

        # Show the progress
        print(f'Videos procesados: {processed_count}')
    
    except RuntimeError as e:
        print(f"Error procesando {video_name}: {e}")

# After the process save all features in your local storage


# Save data for train

In [32]:
for video_key, features in all_features.items():
    for k, v in features.items():
        output_file = os.path.join(feature_path, f'{video_key}.npy')
        with open(output_file, 'wb') as f:
            np.save(f, v)
        print(f'Guardado: {output_file}')

# Process test_features from videos

In [6]:
test_path = "F:/Machine_learning/P_3/test_subset"  #use your local machine path  also  
test_feature_path = "F:/Machine_learning/P_3/test_subset_features"
test_files = os.listdir(test_path)
test_list = [os.path.join(test_path, f) for f in test_files]
feature_type = 'r21d'
args = OmegaConf.load(build_cfg_path(feature_type))
args.video_paths = test_list
args.model_name = 'r2plus1d_18_16_kinetics'
args.device = device

extractor = ExtractR21D(args)

all_features = {}


processed_count = 0


for video_path in args.video_paths:
    processed_count += 1
    video_name = os.path.basename(video_path)
    

  
    try:
        feature_dict = extractor.extract(video_path)
       
        if not feature_dict:
            print(f"No se generaron características para {video_name}")
        else:
            for k, v in feature_dict.items():
        
                video_key = os.path.basename(video_name).replace('.mp4', '')
                if video_key not in all_features:
                    all_features[video_key] = {}
                    all_features[video_key][k] = v

        print(f'Videos procesados: {processed_count}')
    
    except RuntimeError as e:
        print(f"Error procesando {video_name}: {e}")


# Save data for testing


In [10]:
import numpy as np
for video_key, features in all_features.items():
    for k, v in features.items():
        output_file = os.path.join(test_feature_path, f'{video_key}.npy')
        with open(output_file, 'wb') as f:
            np.save(f, v)
        print(f'Guardado: {output_file}')

# Agglomerating method

# Preparando data para procesar validation

In [1]:
from Data_processing_support.data_loading_saving import load_feature_data
from Data_processing_support.feature_summary_techniques import summary_by_mean
import pandas as pd

validation_dir = 'F:\\Machine_learning\\P_3\\validation_subset_features'
all_data , all_names = load_feature_data(feature_dir=validation_dir)
print("size of data : " , len(all_data))
print("size of labels : " , len(all_names))
np_mean=summary_by_mean(all_data)
print("New data frame values and categories :" , np_mean.shape)
print(all_names[0:10])
df = pd.DataFrame(np_mean)
df.to_csv('validation_mean.csv')

Loaded --33Lscn6sk_000004_000014.npy with shape: (11, 512)
Loaded -0dYbFhZsGU_000237_000247.npy with shape: (15, 512)
Loaded -0WZKTu0xNk_000112_000122.npy with shape: (18, 512)
Loaded -1DARulHLgw_000007_000017.npy with shape: (18, 512)
Loaded -1QTRLQSzhQ_000145_000155.npy with shape: (18, 512)
Loaded -2VKVjgNuE0_000000_000010.npy with shape: (11, 512)
Loaded -2VXhGGeOWg_000001_000011.npy with shape: (18, 512)
Loaded -2zDnjMmI5U_000477_000487.npy with shape: (10, 512)
Loaded -3cPJnxtl7U_000095_000105.npy with shape: (15, 512)
Loaded -3oo45vpQV4_000291_000301.npy with shape: (15, 512)
Loaded -4JdZpx3zNk_000268_000278.npy with shape: (18, 512)
Loaded -514AQUrSow_000058_000068.npy with shape: (18, 512)
Loaded -5fnpyU2iE0_000113_000123.npy with shape: (15, 512)
Loaded -5fqwdtpSOY_000013_000023.npy with shape: (9, 512)
Loaded -65aI53dvdE_000022_000032.npy with shape: (18, 512)
Loaded -7E9WiX7QfA_000053_000063.npy with shape: (18, 512)
Loaded -94nreFhQRg_000020_000030.npy with shape: (12, 512

In [2]:
import pandas as pd
import numpy as np

from Cluster_Models.Agglomerate_method import AgglomerativeMethod 
from Data_processing_support.feature_summary_techniques import get_cluster_number,add_true_categories_to_data_frame  , get_all_metrics

cluster_number = get_cluster_number("validation")
print("Expected Number of clusters : " , cluster_number)

cluster_method = AgglomerativeMethod(data=np_mean  , cluster_number=cluster_number , linkage_method='centroid')
cluster_method.fit()
labels = cluster_method.labels
df_mean = pd.DataFrame(np_mean)

df_mean['video'] = all_names
df_mean['cluster'] = labels

df_mean = add_true_categories_to_data_frame(df_mean ,"validation" )

print(df_mean[['video', 'category' ,'cluster' ]].head())

true_labels = df_mean['category']
predicted_labels = df_mean['cluster']

get_all_metrics(predicted_labels, true_labels , np_mean)


Expected Number of clusters :  20
         video          category  cluster
0  --33Lscn6sk  flipping pancake        0
1  -0dYbFhZsGU           texting        0
2  -0WZKTu0xNk  wrapping present        0
3  -1DARulHLgw             situp        0
4  -1QTRLQSzhQ  playing kickball        0
----------------------------------------
Silhouette Score: 0.31437105911649355
----------------------------------------
Adjusted Rand Index: 0.0005027697043898385
----------------------------------------
Mutual Info Index: 0.00910825195506882


# Obetener los resultados finales del Clustering en test

### Cargar data de test y procesar la media

In [15]:
from Data_processing_support.data_loading_saving import load_feature_data
validation_dir = 'F:\\Machine_learning\\P_3\\test_subset_features'
all_data_video , all_names_video = load_feature_data(feature_dir=validation_dir)

Loaded -3T2VPGo2jI_000170_000180.npy with shape: (15, 512)
Loaded -7Wz9S-ZZz4_000006_000016.npy with shape: (15, 512)
Loaded -a1f1ikmdd8_000000_000010.npy with shape: (18, 512)
Loaded -AZMzKjls-k_000174_000184.npy with shape: (15, 512)
Loaded -bGVnGCy2yY_000004_000014.npy with shape: (18, 512)
Loaded -BrNqmFy-6Y_000009_000019.npy with shape: (9, 512)
Loaded -CsBjy8T-II_000029_000039.npy with shape: (18, 512)
Loaded -eOxQpTp5zM_000258_000268.npy with shape: (18, 512)
Loaded -FhZ1JPZYl0_000054_000064.npy with shape: (11, 512)
Loaded -fyfEc1C5Hc_000006_000016.npy with shape: (18, 512)
Loaded -IdatujDsqA_000049_000059.npy with shape: (18, 512)
Loaded -J8jfO0Fp6M_000335_000345.npy with shape: (18, 512)
Loaded -JdfkIKg0w4_000008_000018.npy with shape: (18, 512)
Loaded -Npm2udxeAE_000071_000081.npy with shape: (18, 512)
Loaded -pBHLSZrn3k_000009_000019.npy with shape: (11, 512)
Loaded -RCv-107T5w_000226_000236.npy with shape: (15, 512)
Loaded -rhOaNjvwWo_000008_000018.npy with shape: (9, 512)

## Trabajando con la media para cada dato de sonido en test

In [16]:
from Data_processing_support.data_loading_saving import load_feature_data
from Data_processing_support.feature_summary_techniques import summary_by_mean
import pandas as pd

validation_dir = 'F:\\Machine_learning\\P_3\\test_subset_features'
all_data , all_names = load_feature_data(feature_dir=validation_dir)
print("size of data : " , len(all_data))
print("size of labels : " , len(all_names))
np_mean=summary_by_mean(all_data)
print("New data frame values and categories :" , np_mean.shape)
print(all_names[0:10])
df = pd.DataFrame(np_mean)
df.to_csv('validation_mean.csv')

Loaded -3T2VPGo2jI_000170_000180.npy with shape: (15, 512)
Loaded -7Wz9S-ZZz4_000006_000016.npy with shape: (15, 512)
Loaded -a1f1ikmdd8_000000_000010.npy with shape: (18, 512)
Loaded -AZMzKjls-k_000174_000184.npy with shape: (15, 512)
Loaded -bGVnGCy2yY_000004_000014.npy with shape: (18, 512)
Loaded -BrNqmFy-6Y_000009_000019.npy with shape: (9, 512)
Loaded -CsBjy8T-II_000029_000039.npy with shape: (18, 512)
Loaded -eOxQpTp5zM_000258_000268.npy with shape: (18, 512)
Loaded -FhZ1JPZYl0_000054_000064.npy with shape: (11, 512)
Loaded -fyfEc1C5Hc_000006_000016.npy with shape: (18, 512)
Loaded -IdatujDsqA_000049_000059.npy with shape: (18, 512)
Loaded -J8jfO0Fp6M_000335_000345.npy with shape: (18, 512)
Loaded -JdfkIKg0w4_000008_000018.npy with shape: (18, 512)
Loaded -Npm2udxeAE_000071_000081.npy with shape: (18, 512)
Loaded -pBHLSZrn3k_000009_000019.npy with shape: (11, 512)
Loaded -RCv-107T5w_000226_000236.npy with shape: (15, 512)
Loaded -rhOaNjvwWo_000008_000018.npy with shape: (9, 512)

### ENTRENAMIENTO FINAL

In [4]:
import pandas as pd
import numpy as np

from Cluster_Models.Agglomerate_method import AgglomerativeMethod 
from Data_processing_support.feature_summary_techniques import get_cluster_number,add_true_categories_to_data_frame  , get_all_metrics


cluster_method = AgglomerativeMethod(data=np_mean  , cluster_number=20 , linkage_method='centroid')
cluster_method.fit()
labels = cluster_method.labels
print(len(labels))

1626
1625
1624
1623
1622
1621
1620
1619
1618
1617
1616
1615
1614
1613
1612
1611
1610
1610
1610
1610
1610
1609
1609
1609
1609
1609
1609
1609
1608
1607
1607
1607
1606
1605
1604
1603
1602
1601
1601
1601
1601
1601
1601
1601
1600
1600
1600
1599
1598
1597
1596
1595
1594
1593
1592
1591
1591
1591
1590
1590
1590
1590
1590
1589
1589
1589
1589
1589
1588
1587
1586
1585
1584
1584
1584
1584
1583
1583
1583
1583
1583
1583
1583
1582
1581
1580
1580
1580
1580
1579
1578
1578
1578
1578
1578
1578
1578
1578
1578
1578
1578
1578
1578
1578
1578
1578
1578
1578
1578
1578
1577
1577
1577
1577
1577
1577
1577
1577
1577
1577
1577
1577
1577
1577
1577
1577
1577
1577
1577
1577
1577
1577
1577
1577
1577
1577
1577
1577
1577
1577
1576
1575
1575
1575
1575
1575
1575
1575
1575
1575
1574
1573
1572
1571
1570
1569
1568
1568
1568
1568
1568
1567
1567
1567
1567
1566
1565
1564
1563
1562
1561
1561
1561
1561
1561
1561
1561
1561
1561
1561
1561
1561
1561
1561
1561
1560
1560
1560
1560
1560
1560
1560
1560
1560
1559
1559
1559
1559
1559
1559


# resultados finales

In [17]:
# cargamos el test_subset_10.csv
df_test = pd.read_csv('test_subset_10.csv')

# los df_test youtube_id los pasamos a una lista
youtube_id = df_test['youtube_id'].tolist()
#print(youtube_id)


df['video'] = all_names
df['predict_label'] =labels

# extraemos de df los videos que estan en youtube_id
df = df[df['video'].isin(youtube_id)]

print(df[['video','predict_label']])
df[['video','predict_label']].to_csv("results_Agglomerative.csv")


            video  predict_label
1     -7Wz9S-ZZz4              0
2     -a1f1ikmdd8              0
4     -bGVnGCy2yY              0
5     -BrNqmFy-6Y              0
6     -CsBjy8T-II              0
...           ...            ...
1620  ZTTEkAxEnUs              0
1622  zujZagp-4jQ              0
1623  ZuvChCAjbak              0
1624  ZxpwgIZg4lI              0
1625  zz1YMml9Z6k              0

[805 rows x 2 columns]
